In [5]:
import os
import xml.etree.ElementTree as ET

def convert_coordinates(size, box):
    dw = 1.0 / size[0]
    dh = 1.0 / size[1]
    x = (box[0] + box[2]) / 2.0
    y = (box[1] + box[3]) / 2.0
    w = box[2] - box[0]
    h = box[3] - box[1]
    x = x * dw
    w = w * dw
    y = y * dh
    h = h * dh
    return (x, y, w, h)


In [6]:

def convert_annotation(xml_file, output_folder):
    tree = ET.parse(xml_file)
    root = tree.getroot()

    image_name = root.find('filename').text
    image_width = int(root.find('size/width').text)
    image_height = int(root.find('size/height').text)

    with open(os.path.join(output_folder, os.path.splitext(image_name)[0] + '.txt'), 'w') as out_file:
        for obj in root.iter('object'):
            cls = obj.find('name').text
            if cls == 'head':
                cls_id = 0
                xmlbox = obj.find('bndbox')
                b = (float(xmlbox.find('xmin').text), float(xmlbox.find('ymin').text), float(xmlbox.find('xmax').text), float(xmlbox.find('ymax').text))
                bb = convert_coordinates((image_width, image_height), b)
                out_file.write(str(cls_id) + " " + " ".join([str(a) for a in bb]) + '\n')

def get_processed_files_list(output_folder):
    processed_files = set()
    for file in os.listdir(output_folder):
        if file.endswith('.txt'):
            processed_files.add(os.path.splitext(file)[0] + '.xml')
    return processed_files


In [16]:

annotations_folder = 'Annotations'
output_folder = 'labels'

os.makedirs(output_folder, exist_ok=True)

processed_files = get_processed_files_list(output_folder)
total_files = len(os.listdir(annotations_folder))
processed_files_count = 0


In [20]:
try:
    for xml_file in os.listdir(annotations_folder):
        if xml_file.endswith('.xml') and xml_file not in processed_files:
            try:
                convert_annotation(os.path.join(annotations_folder, xml_file), output_folder)
                processed_files_count += 1
                print(f"Progress: {processed_files_count}/{total_files} files processed")
            except Exception as e:
                print(f"Error processing file {xml_file}: {str(e)}")
except Exception as e:
    print(f"Error reading directory {annotations_folder}: {str(e)}")


Error processing file mov_007_121343.xml: 'NoneType' object has no attribute 'text'
Error processing file mov_007_121344.xml: 'NoneType' object has no attribute 'text'
Error processing file mov_007_121345.xml: 'NoneType' object has no attribute 'text'
Error processing file mov_007_121346.xml: 'NoneType' object has no attribute 'text'
Error processing file mov_007_121347.xml: 'NoneType' object has no attribute 'text'
Error processing file mov_007_121348.xml: 'NoneType' object has no attribute 'text'
Error processing file mov_007_121349.xml: 'NoneType' object has no attribute 'text'
Error processing file mov_007_121350.xml: 'NoneType' object has no attribute 'text'
Error processing file mov_007_121351.xml: 'NoneType' object has no attribute 'text'
Progress: 391/224740 files processed
Progress: 392/224740 files processed
Progress: 393/224740 files processed
Progress: 394/224740 files processed
Progress: 395/224740 files processed
Progress: 396/224740 files processed
Progress: 397/224740 f

In [26]:
test_image_path = "images/mov_015_050699.jpeg"
test_label_path = "labels/mov_015_050699.txt"


import matplotlib.pyplot as plt
import matplotlib.patches as patches
from PIL import Image

def visualize_yolo(image_path, yolo_annotations_file):
    # Open the image
    img = Image.open(image_path)

    # Create figure and axes
    fig, ax = plt.subplots(1)
    ax.imshow(img)

    # Read YOLO annotations from file
    with open(yolo_annotations_file, 'r') as f:
        yolo_annotations = f.read().splitlines()

    # Parse YOLO annotations and draw bounding boxes
    for annotation in yolo_annotations:
        class_name, x_center, y_center, width, height = annotation.split()
        x_center, y_center, width, height = float(x_center), float(y_center), float(width), float(height)

        # Convert YOLO coordinates to image coordinates
        img_width, img_height = img.size
        xmin = int((x_center - width / 2) * img_width)
        ymin = int((y_center - height / 2) * img_height)
        xmax = int((x_center + width / 2) * img_width)
        ymax = int((y_center + height / 2) * img_height)

        # Create a Rectangle patch
        rect = patches.Rectangle((xmin, ymin), xmax - xmin, ymax - ymin, linewidth=2, edgecolor='r', facecolor='none')

        # Add the patch to the Axes
        ax.add_patch(rect)


    # Show the image with bounding boxes
    plt.show()
